In [7]:
import os
import re
import json
import glob
import numpy as np
import pandas as pd
import geopandas as gpd
from datetime import datetime
from shapely.geometry import box, Point
from rasterio.windows import Window
import rasterio
import matplotlib.pyplot as plt
from tqdm import tqdm

In [8]:
BASE_PATH = '/home/yurii/.cache/kagglehub/datasets/isaienkov/deforestation-in-ukraine/versions/1'
GEOJSON_PATH = os.path.join(BASE_PATH, 'deforestation_labels.geojson')
OUTPUT_DIR = '/home/yurii/Programming/Quantum_Test_Data'
PATCH_SIZE = 500
MIN_DAYS_BETWEEN = 60

In [9]:
def parse_folder_name(folder_name):
    """Витягує дату та географічний тайл з назви папки"""
    try:
        # Приклад: S2A_MSIL1C_20160212T084052_N0201_R064_T36UYA_20160212T084510
        date_match = re.search(r'(\d{8})T\d{6}', folder_name)
        
        # ПРАВИЛЬНО: шукаємо тільки тайли формату T36UYA (починаються з 'T')
        tile_match = re.search(r'_([T][A-Z0-9]{5})_', folder_name)
        
        if not date_match or not tile_match:
            return None
        
        date_str = date_match.group(1)
        tile = tile_match.group(1)
        
        return {
            'date': datetime.strptime(date_str, '%Y%m%d'),
            'tile': tile,
            'folder_name': folder_name
        }
    except Exception as e:
        print(f"Помилка при обробці папки {folder_name}: {e}")
        return None

def find_tci_path(folder_path):
    """Знаходить шлях до TCI.jp2 файлу в структурі папок Sentinel-2"""
    pattern = os.path.join(folder_path, "*.SAFE", "GRANULE", "*", "IMG_DATA", "*_TCI.jp2")
    matches = glob.glob(pattern)
    return matches[0] if matches else None

def get_season(date):
    """Визначає сезон за датою"""
    month = date.month
    if month in [12, 1, 2]:
        return 'winter'
    elif month in [3, 4, 5]:
        return 'spring'
    elif month in [6, 7, 8]:
        return 'summer'
    else:
        return 'autumn'

def get_tile_bounds(image_path):
    """Отримує географічні межі знімку"""
    with rasterio.open(image_path) as src:
        return src.bounds

def crop_patch_around_centroid(image_path, centroid, patch_size=500):
    """
    Вирізає патч 500x500 навколо центроїда з прив'язкою до сітки
    """
    try:
        with rasterio.open(image_path) as src:
            # Перетворюємо геокоординати в піксельні
            col, row = src.index(centroid.x, centroid.y)
            
            # Знаходимо початок сіткової комірки
            grid_col = (col // patch_size) * patch_size
            grid_row = (row // patch_size) * patch_size
            
            # Розраховуємо зміщення для центрування
            offset_col = col - grid_col
            offset_row = row - grid_row
            
            # Визначаємо початок патча так, щоб центр вирубки був у центрі
            col_start = grid_col + (patch_size // 2) - offset_col
            row_start = grid_row + (patch_size // 2) - offset_row
            
            # Захист від виходу за межі зображення
            col_start = max(0, min(col_start, src.width - patch_size))
            row_start = max(0, min(row_start, src.height - patch_size))
            
            # Створюємо вікно
            window = Window(col_start, row_start, patch_size, patch_size)
            
            # Читаємо дані (тільки RGB канали для початку)
            data = src.read([1, 2, 3], window=window)  # R, G, B
            data = np.transpose(data, (1, 2, 0))  # Перетворюємо в (H, W, C)
            
            # Нормалізація до [0, 1]
            data = data.astype(np.float32) / 65535.0
            
            return data, {
                'top_left': (col_start, row_start),
                'window': window,
                'transform': src.window_transform(window),
                'grid_position': (grid_row // patch_size, grid_col // patch_size)
            }
    except Exception as e:
        print(f"Помилка при обробці {image_path}: {e}")
        return None, None

In [10]:
print("🔍 Збір інформації про папки...")
folder_data = []

for folder_name in os.listdir(BASE_PATH):
    folder_path = os.path.join(BASE_PATH, folder_name)
    if not os.path.isdir(folder_path) or 'deforestation_labels' in folder_name:
        continue
    
    # Парсимо назву папки
    info = parse_folder_name(folder_name)
    if not info:
        continue
    
    # Знаходимо TCI.jp2
    tci_path = find_tci_path(folder_path)
    if not tci_path:
        continue
    
    # Додаємо інформацію про розмір зображення
    with rasterio.open(tci_path) as src:
        width, height = src.width, src.height
    
    folder_data.append({
        'date': info['date'],
        'tile': info['tile'],
        'folder_name': folder_name,
        'tci_path': tci_path,
        'width': width,
        'height': height,
        'season': get_season(info['date'])
    })

print(f"✅ Знайдено {len(folder_data)} супутникових знімків")

🔍 Збір інформації про папки...
✅ Знайдено 50 супутникових знімків


In [11]:
folder_data[0]['tci_path']

'/home/yurii/.cache/kagglehub/datasets/isaienkov/deforestation-in-ukraine/versions/1/S2B_MSIL1C_20180726T084009_N0206_R064_T36UXA_20180726T104227/S2B_MSIL1C_20180726T084009_N0206_R064_T36UXA_20180726T104227.SAFE/GRANULE/L1C_T36UXA_A007240_20180726T084437/IMG_DATA/T36UXA_20180726T084009_TCI.jp2'

In [12]:
print("🌳 Завантаження даних про вирубки...")
df = gpd.read_file(GEOJSON_PATH)

# 3. Визначення CRS та перетворення вирубок
sample_img = folder_data[0]['tci_path']
with rasterio.open(sample_img) as src:
    raster_crs = src.crs

print(f"🌍 CRS супутникових знімків: {raster_crs}")
df_r = df.to_crs(raster_crs)

🌳 Завантаження даних про вирубки...
🌍 CRS супутникових знімків: EPSG:32636


In [13]:
# 4. Групування вирубок за тайлами
print("📍 Групування вирубок за географічними тайлами...")
tile_bounds = {}
deforestation_by_tile = {'T36UYA': [], 'T36UXA': []}

# Отримуємо межі для кожного тайлу
for tile in ['T36UYA', 'T36UXA']:
    for info in folder_data:
        if info['tile'] == tile:
            tile_bounds[tile] = get_tile_bounds(info['tci_path'])
            break

# Відносимо вирубки до тайлів
for idx, row in df_r.iterrows():
    for tile, bounds in tile_bounds.items():
        tile_polygon = box(bounds.left, bounds.bottom, bounds.right, bounds.top)
        if row.geometry.intersects(tile_polygon):
            deforestation_by_tile[tile].append({
                'id': idx,
                'geometry': row.geometry,
                'properties': row.drop('geometry').to_dict()
            })
            break

print(f"  • T36UYA: {len(deforestation_by_tile['T36UYA'])} вирубок")
print(f"  • T36UXA: {len(deforestation_by_tile['T36UXA'])} вирубок")

📍 Групування вирубок за географічними тайлами...
  • T36UYA: 3500 вирубок
  • T36UXA: 1646 вирубок


In [14]:
# import multiprocessing
# from tqdm import tqdm
# from shapely.geometry import Point
# from shapely.geometry import box
# import json
# from datetime import date # Потрібно для обробки об'єктів date

# # --- ЕМУЛЯЦІЯ/КОНСТАНТИ ---
# # Припускаємо, що ці змінні/функції визначені десь вище у вашому коді:
# # folder_data, deforestation_by_tile, MIN_DAYS_BETWEEN, get_tile_bounds

# # Файл, куди будуть зберігатися всі створені пари
# PAIRS_OUTPUT_FILE = 'seasonal_pairs_metadata.jsonl' 
# # Глобальний лок для безпечного запису в спільний файл (необхідний для multiprocessing)
# FILE_LOCK = multiprocessing.Lock()


# # --- ДОПОМІЖНА ФУНКЦІЯ ДЛЯ СЕРІАЛІЗАЦІЇ ---
# def json_serial(obj):
#     """JSON serializer for objects not serializable by default json code"""
#     if isinstance(obj, date):
#         return obj.isoformat()
#     # Серіалізуємо об'єкти Shapely Geometry (якщо вони є)
#     if hasattr(obj, '__geo_interface__'):
#         return obj.__geo_interface__
#     raise TypeError ("Type %s not serializable" % type(obj))

# # --- ФУНКЦІЯ ДЛЯ ПАРАЛЕЛЬНОЇ ОБРОБКИ (З БЕЗПЕЧНИМ ЗАПИСОМ) ---
# def create_pairs_for_deforestation(defor_data):
#     """
#     Створює сезонні пари зображень для однієї події вирубки та записує їх у файл.

#     Args:
#         defor_data (tuple): Кортеж, що містить:
#                             (defor, tile, summer_images, other_seasons)

#     Returns:
#         int: Кількість успішно створених та збережених пар.
#     """
#     defor, tile, summer_images, other_seasons = defor_data
#     local_pairs_count = 0
#     centroid = defor['geometry'].centroid

#     # Тимчасовий список для збору пар, які згенерував цей процес
#     pairs_to_write = []

#     # Створюємо пари для кожного сезону
#     for season_name, season_images in other_seasons.items():
#         for summer_img in summer_images:
            
#             # Отримання меж для перевірки видимості
#             try:
#                 summer_bounds = box(*get_tile_bounds(summer_img['tci_path']))
#             except Exception:
#                 continue
            
#             # Перевірка видимості centroid у літньому знімку
#             if not Point(centroid).within(summer_bounds):
#                 continue
                
#             for other_img in season_images:
#                 days_diff = abs((other_img['date'] - summer_img['date']).days)
                
#                 # Перевіряємо мінімальний часовий інтервал
#                 if days_diff < MIN_DAYS_BETWEEN:
#                     continue
                
#                 # Перевіряємо, чи вирубка видима в "іншому" знімку
#                 try:
#                     other_bounds = box(*get_tile_bounds(other_img['tci_path']))
#                 except Exception:
#                     continue
                    
#                 if not Point(centroid).within(other_bounds):
#                     continue
                
#                 # Замість pairs.append(), додаємо до локального списку
#                 pair = {
#                     'summer_img': summer_img,
#                     'other_img': other_img,
#                     'season_pair': f'summer_{season_name}',
#                     'deforestation': defor,
#                     'centroid': centroid,
#                     'tile': tile
#                 }
                
#                 pairs_to_write.append(pair)
#                 local_pairs_count += 1
                
#     # --- БЕЗПЕЧНИЙ ЗАПИС У ФАЙЛ ---
#     if pairs_to_write:
#         # Блокуємо файл, щоб інший процес не записував одночасно
#         with FILE_LOCK:
#             with open(PAIRS_OUTPUT_FILE, 'a', encoding='utf-8') as f:
#                 for pair in pairs_to_write:
#                     # Серіалізуємо об'єкт перед записом
#                     json_line = json.dumps(pair, default=json_serial)
#                     f.write(json_line + '\n')
                    
#     return local_pairs_count

# # --- ОСНОВНИЙ БЛОК ПАРАЛЕЛЬНОЇ ОБРОБКИ ---

# def run_pair_creation():
#     """Головна функція для запуску створення пар."""
    
#     print("🔄 Створення сезонних пар та запис на диск...")

#     # 1. Скидання файлу (або перевірка на існування для відновлення)
#     if os.path.exists(PAIRS_OUTPUT_FILE):
#         print(f"⚠️ Файл {PAIRS_OUTPUT_FILE} існує. Буде додано нові дані.")
#     else:
#         print(f"📝 Створення нового файлу: {PAIRS_OUTPUT_FILE}")

#     # 2. Збір всіх завдань
#     tasks = []
#     tiles_to_process = ['T36UYA', 'T36UXA']
    
#     for tile in tiles_to_process:
#         # Фільтруємо зображення для поточного тайлу (це не змінюється)
#         tile_images = [img for img in folder_data if img['tile'] == tile]
        
#         # Зображення для кожного сезону (це не змінюється)
#         summer_images = [img for img in tile_images if img['season'] == 'summer']
#         other_seasons = {
#             'autumn': [img for img in tile_images if img['season'] == 'autumn'],
#             'winter': [img for img in tile_images if img['season'] == 'winter'],
#             'spring': [img for img in tile_images if img['season'] == 'spring']
#         }
        
#         # Формуємо список завдань: одна вирубка = одне завдання
#         for defor in deforestation_by_tile[tile]:
#             tasks.append((defor, tile, summer_images, other_seasons))

#     num_processes = 7 # Використовуємо 4 ядра, як просили
    
#     print(f"🛠️ Запуск паралельної обробки на {num_processes} процесах для {len(tasks)} подій вирубки...")

#     # 3. Запуск Pool для паралельного виконання
#     with multiprocessing.Pool(processes=num_processes) as pool:
#         # Використовуємо imap_unordered для паралельного виконання та tqdm для прогресу
#         results = list(tqdm(pool.imap_unordered(create_pairs_for_deforestation, tasks), 
#                              total=len(tasks), 
#                              desc="Генерація пар та запис на диск"))
        
#         total_pairs_created = sum(results)

#     print(f"✅ Створено та збережено {total_pairs_created} сезонних пар у файлі {PAIRS_OUTPUT_FILE}")

    
# run_pair_creation()

In [39]:
import os
import re
import json
import glob
import numpy as np
import pandas as pd
import geopandas as gpd
from datetime import datetime, date
from shapely.geometry import box, Point, shape
from rasterio.windows import Window
import rasterio
import matplotlib.pyplot as plt
from tqdm import tqdm
from multiprocessing import Pool, cpu_count, current_process
import warnings

warnings.filterwarnings('ignore', category=UserWarning)

OUTPUT_DIR = '/home/yurii/Programming/Quantum_Test_Data' 
PAIRS_METADATA_FILE = 'seasonal_pairs_metadata.jsonl'
PATCH_SIZE_FINAL = 512
# 🛑 ЛІМІТ: Зупиняємо, коли буде створено 300,000 тренувальних пар
TRAIN_PAIRS_LIMIT = 5000 
# 🛑 ОБМЕЖЕННЯ ЯДЕР: Використовуємо лише 2 ядра
NUM_WORKERS = 2 
H_GT = np.eye(3) 

# ІНШІ ДОПОМІЖНІ ФУНКЦІЇ (parse_folder_name, find_band_path, get_tile_bounds,
# get_season, crop_patch_around_centroid) - ПРИПУСКАЄМО, ЩО ВИЗНАЧЕНІ ПРАВИЛЬНО.

# ======================================================
# ФУНКЦІЯ 1: ІТЕРАТИВНЕ ЧИТАННЯ (ГЕНЕРАТОР)
# ======================================================
# ======================================================
# ФУНКЦІЯ 1: ІТЕРАТИВНЕ ЧИТАННЯ (ГЕНЕРАТОР)
# ======================================================
def pair_generator():
    """
    Генератор, який ліниво читає пари з .jsonl та виконує парсинг.
    """
    try:
        with open(PAIRS_METADATA_FILE, 'r', encoding='utf-8') as f:
            for i, line in enumerate(f):
                try:
                    pair = json.loads(line)
                    
                    # 1. Парсинг дат
                    pair['summer_img']['date'] = datetime.strptime(pair['summer_img']['date'].split('T')[0], '%Y-%m-%d').date()
                    pair['other_img']['date'] = datetime.strptime(pair['other_img']['date'].split('T')[0], '%Y-%m-%d').date()
                    
                    # 2. Парсинг центроїда у Shapely Point (обов'язково для .__geo_interface__)
                    # pair['centroid'] є об'єктом GeoJSON {"type": "Point", "coordinates": [...]}.
                    # Ми перетворюємо його на об'єкт Shapely, щоб викликати .__geo_interface__ пізніше.
                    pair['centroid'] = shape(pair['centroid'])
                    
                    # 3. Геометрію MultiPolygon залишаємо як GeoJSON-словник (це правильно для json.dump).
                    
                    yield i, pair # Повертаємо індекс та словник пари
                except Exception as e:
                    # print(f"Помилка парсингу рядка {i} в {PAIRS_METADATA_FILE}: {e}")
                    continue
    except FileNotFoundError:
        print(f"❌ Файл {PAIRS_METADATA_FILE} не знайдено.")

# ======================================================
# ФУНКЦІЯ 2: ВИПАДКОВИЙ ПОДІЛ TRAIN/VAL
# ======================================================
# Словник для зберігання ID, які вже потрапили в 'val'
VAL_DEFOR_IDS_CACHE = {} 
VAL_PROBABILITY = 0.2 # 20% для валідації

def get_split(deforestation_id):
    """Випадково визначає TRAIN або VAL, але фіксує ID у кеші."""
    
    # 1. Якщо ID вже є в кеші, повертаємо його
    if deforestation_id in VAL_DEFOR_IDS_CACHE:
        return VAL_DEFOR_IDS_CACHE[deforestation_id]
    
    # 2. Якщо ID новий, робимо випадковий вибір
    if np.random.rand() < VAL_PROBABILITY:
        split = 'val'
    else:
        split = 'train'
        
    # 3. Зберігаємо у кеші та повертаємо
    VAL_DEFOR_IDS_CACHE[deforestation_id] = split
    return split


# ======================================================
# ФУНКЦІЯ 3: ПАРАЛ. ОБРОБКА ТА ЗБЕРІГАННЯ (ОНОВЛЕНО З ЛОГАМИ)
# ======================================================
def process_single_pair_limited(task):
    """
    Обробляє та зберігає патчі у форматі (512, 512, 6) з деталізованим логуванням.
    """
    i, pair_data, output_dir, patch_size, h_gt, split = task
    
    # 0. Налаштування логування та шляхів
    process_name = f"Proc-{current_process().pid}"
    
    if current_process()._config is None:
        current_process()._config = {'sem_wait_max': 1} 
    
    defor_id = pair_data['deforestation']['id']
    print(f"[{process_name}] 🔄 Початок обробки ID={defor_id}, індекс={i}")
    
    # Визначення шляхів (ПРИПУСКАЄМО, що BASE_PATH визначено на коректний корінь даних)
    BASE_PATH = '/home/yurii/.cache/kagglehub/datasets/isaienkov/deforestation-in-ukraine/versions/1'
    folder_summer = os.path.join(BASE_PATH, pair_data['summer_img']['folder_name'])
    folder_other = os.path.join(BASE_PATH, pair_data['other_img']['folder_name'])

    # 1. Вирізаємо патчі (512x512x6)
    try:
        patch_summer, _ = read_6_channel_patch(folder_summer, pair_data['centroid'], patch_size)
        patch_other, _ = read_6_channel_patch(folder_other, pair_data['centroid'], patch_size)
    except Exception as e:
        print(f"[{process_name}] ❌ Помилка читання растру для ID={defor_id}: {e}")
        return None
    
    if patch_summer is None or patch_other is None:
        print(f"[{process_name}] ⚠️ Пропущено ID={defor_id}: Patches є порожніми (за межами знімка або відсутність смуг).")
        return None
    
    # 2. Зберігання та Створення Папок
    try:
        pair_dir = os.path.join(output_dir, split, f"defor_{defor_id}_{i:06d}")
        
        if not os.path.exists(pair_dir):
            os.makedirs(pair_dir, exist_ok=True)
            print(f"[{process_name}] ✅ Створено папку: {pair_dir}")
        else:
            print(f"[{process_name}] 📁 Папка вже існує: {pair_dir}")

        # Зберігаємо патчі та Гомографію
        np.save(os.path.join(pair_dir, 'img1.npy'), patch_summer) 
        np.save(os.path.join(pair_dir, 'img2.npy'), patch_other)
        np.save(os.path.join(pair_dir, 'homography.npy'), h_gt) 
        
        # 3. Зберігаємо метадані (Фікс GeoJSON)
        metadata = {
            'img1_path': pair_data['summer_img']['tci_path'],
            'img2_path': pair_data['other_img']['tci_path'],
            'date_img1': pair_data['summer_img']['date'].isoformat(),
            'date_img2': pair_data['other_img']['date'].isoformat(),
            'season_pair': pair_data['season_pair'],
            'deforestation_id': defor_id,
            
            # 🛑 ФІКС ПОМИЛКИ: Центроїд (Shapely Point) використовує .__geo_interface__
            'centroid': pair_data['centroid'].__geo_interface__, 
            'tile': pair_data['tile'],
            
            # 🛑 ФІКС ПОМИЛКИ: Геометрія (Словник GeoJSON) передається напряму
            'defor_geometry_geojson': pair_data['deforestation']['geometry'],
        }
        
        with open(os.path.join(pair_dir, 'metadata.json'), 'w') as f:
            json.dump(metadata, f, indent=2)
            
        print(f"[{process_name}] 💾 Успішно збережено в {split}/{os.path.basename(pair_dir)}")
        
        return split 

    except Exception as e:
        print(f"[{process_name}] 🔴 Критична помилка при записі на диск ID={defor_id}. Помилка: {e}")
        return None

In [40]:
# ======================================================
# ГОЛОВНА ЛОГІКА (З ЛІМІТОМ ТА ІТЕРАЦІЯМИ)
# ======================================================
def run_limited_generation():
    
    print(f"⚙️ Використовуємо {NUM_WORKERS} процесорів.")
    print(f"🎯 Ліміт тренувальних пар: {TRAIN_PAIRS_LIMIT}")
    
    # Лічильники
    train_count = 0
    val_count = 0
    total_pairs_processed = 0
    
    # Налаштування директорій
    os.makedirs(os.path.join(OUTPUT_DIR, 'train'), exist_ok=True)
    os.makedirs(os.path.join(OUTPUT_DIR, 'val'), exist_ok=True)

    # Використовуємо пул для запуску
    with Pool(NUM_WORKERS) as pool:
        
        # Ітерація над лінивим генератором
        pair_iter = pair_generator()
        
        # Запускаємо перший "батч" завдань, щоб пул не простоював
        BATCH_SIZE = NUM_WORKERS * 4
        
        # --- ФАЗА 1: Збір та запуск першого батчу (виправлено розпакування) ---
        initial_tasks = []
        
        # Правильне розпакування: (i, pair) повертає сам генератор
        # Використовуємо next(pair_iter) для отримання наступного елемента
        
        for _ in range(BATCH_SIZE):
            try:
                # Генератор повертає: i, pair_data
                i, pair_data = next(pair_iter) 
                
                # Тепер pair_data є словником, а не кортежем, тому ['deforestation'] працює
                split = get_split(pair_data['deforestation']['id'])
                
                initial_tasks.append((i, pair_data, OUTPUT_DIR, PATCH_SIZE_FINAL, H_GT, split))
                total_pairs_processed += 1
            except StopIteration:
                break # Генератор вичерпано раніше
            except Exception:
                # Обробка помилок парсингу/отримання ID
                continue
            
        print(f"⚡️ Запуск {len(initial_tasks)} початкових завдань...")
        
        if not initial_tasks:
            print("❌ Не вдалося згенерувати жодного початкового завдання. Перевірте файл JSONL.")
            return

        # Запускаємо перші завдання
        async_results = pool.map_async(process_single_pair_limited, initial_tasks)
        
        # --- ФАЗА 2: Основний цикл обробки ---
        pbar = tqdm(total=TRAIN_PAIRS_LIMIT, desc="Створено TRAIN пар")
        
        while train_count < TRAIN_PAIRS_LIMIT:
            
            # 2. Очікуємо на результати попереднього батчу
            try:
                # Очікуємо, поки буде готовий хоча б один результат
                if async_results.ready():
                    results = async_results.get()
                    
                    # 3. Оновлення лічильників та прогресу
                    for split_result in results:
                        if split_result == 'train':
                            train_count += 1
                        elif split_result == 'val':
                            val_count += 1
                            
                    pbar.update(train_count - pbar.n)
                    
                    # 4. Перевірка ліміту
                    if train_count >= TRAIN_PAIRS_LIMIT:
                        break
                        
                    # 5. Створення та запуск нового батчу завдань (виправлено розпакування)
                    new_tasks = []
                    
                    for _ in range(BATCH_SIZE):
                        try:
                            # Отримуємо наступний елемент
                            i, pair_data = next(pair_iter) 
                        except StopIteration:
                            break # Генератор вичерпано
                        except Exception:
                            continue # Помилка при отриманні/парсингу наступного елемента

                        split = get_split(pair_data['deforestation']['id'])
                        
                        # Якщо це тренувальна пара і ми близькі до ліміту, не додаємо її
                        if split == 'train' and train_count + len(new_tasks) >= TRAIN_PAIRS_LIMIT:
                             break
                             
                        new_tasks.append((i, pair_data, OUTPUT_DIR, PATCH_SIZE_FINAL, H_GT, split))
                        total_pairs_processed += 1
                        
                    if not new_tasks:
                        break # Генератор вичерпано
                        
                    async_results = pool.map_async(process_single_pair_limited, new_tasks)
                    
            except Exception as e:
                # Обробка помилок пулу
                print(f"\nКритична помилка в пулі: {e}")
                break
            
            # Якщо завдання не готове, чекаємо
            if not async_results.ready():
                pbar.set_description(f"Обробка ({train_count} train / {val_count} val)")
                plt.pause(0.1) # Коротка пауза для оновлення GUI/потоків

        pbar.close()

    print(f"\n✅ ГЕНЕРАЦІЮ ЗАВЕРШЕНО.")
    print(f"📊 Фінальний результат:")
    print(f"   • Створено TRAIN пар: {train_count}")
    print(f"   • Створено VAL пар: {val_count}")
    print(f"   • Оброблені рядки з JSONL: {total_pairs_processed}")

In [ ]:
run_limited_generation()

⚙️ Використовуємо 2 процесорів.
🎯 Ліміт тренувальних пар: 5000
⚡️ Запуск 8 початкових завдань...


[Proc-647287] 🔄 Початок обробки ID=12, індекс=0

Створено TRAIN пар:   0%|          | 0/5000 [00:00<?, ?it/s]

[Proc-647288] 🔄 Початок обробки ID=12, індекс=1

Обробка (0 train / 0 val):   0%|          | 0/5000 [00:00<?, ?it/s]

...

Обробка (4098 train / 1590 val):  82%|████████▏ | 4098/5000 [47:22<08:23,  1.79it/s]

[Proc-647288] 🔄 Початок обробки ID=97, індекс=5689

[Proc-647288] ✅ Створено папку: /home/yurii/Programming/Quantum_Test_Data/train/defor_97_005689
[Proc-647288] 💾 Успішно збережено в train/defor_97_005689
[Proc-647288] 🔄 Початок обробки ID=97, індекс=5690


[Proc-647287] ✅ Створено папку: /home/yurii/Programming/Quantum_Test_Data/train/defor_97_005688


[Proc-647287] 💾 Успішно збережено в train/defor_97_005688
[Proc-647287] 🔄 Початок обробки ID=97, індекс=5691


In [ ]:
# import os
# import re
# import json
# import glob
# import numpy as np
# import pandas as pd
# import geopandas as gpd
# from datetime import datetime, date
# from shapely.geometry import box, Point, shape
# from rasterio.windows import Window
# import rasterio
# import matplotlib.pyplot as plt
# from tqdm import tqdm
# from multiprocessing import Pool, cpu_count, current_process
# import warnings

# warnings.filterwarnings('ignore', category=UserWarning)

# OUTPUT_DIR = '/home/yurii/Programming/Quantum_Test_Data' 
# PAIRS_METADATA_FILE = 'seasonal_pairs_metadata.jsonl'
# PATCH_SIZE_FINAL = 512
# # 🛑 ЛІМІТ: Зупиняємо, коли буде створено 300,000 тренувальних пар
# TRAIN_PAIRS_LIMIT = 300000 
# # 🛑 ОБМЕЖЕННЯ ЯДЕР: Використовуємо лише 2 ядра
# NUM_WORKERS = 2 
# H_GT = np.eye(3) 

# # ІНШІ ДОПОМІЖНІ ФУНКЦІЇ (parse_folder_name, find_band_path, get_tile_bounds,
# # get_season, crop_patch_around_centroid) - ПРИПУСКАЄМО, ЩО ВИЗНАЧЕНІ ПРАВИЛЬНО.

# # ======================================================
# # ФУНКЦІЯ 1: ІТЕРАТИВНЕ ЧИТАННЯ (ГЕНЕРАТОР)
# # ======================================================
# def pair_generator():
#     """
#     Генератор, який ліниво читає пари з .jsonl та виконує парсинг.
#     Використовується для економії RAM.
#     """
#     try:
#         with open(PAIRS_METADATA_FILE, 'r', encoding='utf-8') as f:
#             for i, line in enumerate(f):
#                 try:
#                     pair = json.loads(line)
                    
#                     # Парсинг дат
#                     pair['summer_img']['date'] = datetime.strptime(pair['summer_img']['date'].split('T')[0], '%Y-%m-%d').date()
#                     pair['other_img']['date'] = datetime.strptime(pair['other_img']['date'].split('T')[0], '%Y-%m-%d').date()
                    
#                     # Парсинг центроїда
#                     pair['centroid'] = shape(pair['centroid'])
                    
#                     yield i, pair # Повертаємо індекс та пару
#                 except Exception as e:
#                     #print(f"Помилка парсингу рядка {i} в {PAIRS_METADATA_FILE}: {e}")
#                     continue
#     except FileNotFoundError:
#         print(f"❌ Файл {PAIRS_METADATA_FILE} не знайдено.")

# # ======================================================
# # ФУНКЦІЯ 2: ВИПАДКОВИЙ ПОДІЛ TRAIN/VAL
# # ======================================================
# # Словник для зберігання ID, які вже потрапили в 'val'
# VAL_DEFOR_IDS_CACHE = {} 
# VAL_PROBABILITY = 0.2 # 20% для валідації

# def get_split(deforestation_id):
#     """Випадково визначає TRAIN або VAL, але фіксує ID у кеші."""
    
#     # 1. Якщо ID вже є в кеші, повертаємо його
#     if deforestation_id in VAL_DEFOR_IDS_CACHE:
#         return VAL_DEFOR_IDS_CACHE[deforestation_id]
    
#     # 2. Якщо ID новий, робимо випадковий вибір
#     if np.random.rand() < VAL_PROBABILITY:
#         split = 'val'
#     else:
#         split = 'train'
        
#     # 3. Зберігаємо у кеші та повертаємо
#     VAL_DEFOR_IDS_CACHE[deforestation_id] = split
#     return split

# # ======================================================
# # ФУНКЦІЯ 3: ПАРАЛ. ОБРОБКА ТА ЗБЕРЕЖЕННЯ
# # ======================================================

# def process_single_pair_limited(task):
#     """
#     Обробляє та зберігає патчі. Використовується для Pool.starmap.
#     """
#     i, pair_data, output_dir, patch_size, h_gt, split = task
    
#     if current_process()._config is None:
#         # Ініціалізація, щоб уникнути помилок Pickling/multiprocessing
#         current_process()._config = {'sem_wait_max': 1} 

#     # Перевірка: Якщо це тренувальна пара і ми перевищили ліміт, повертаємо None
#     # Ця перевірка є лише приблизною, оскільки лічильник оновлюється в main().
#     # Точний контроль ліміту відбувається в main().
    
#     # Вирізаємо патчі
#     patch_summer, _ = crop_patch_around_centroid(
#         pair_data['summer_img']['tci_path'], pair_data['centroid'], patch_size
#     )
    
#     patch_other, _ = crop_patch_around_centroid(
#         pair_data['other_img']['tci_path'], pair_data['centroid'], patch_size
#     )
    
#     if patch_summer is None or patch_other is None:
#         return None
    
#     # Зберігання
#     defor_id = pair_data['deforestation']['id']
#     pair_dir = os.path.join(output_dir, split, f"defor_{defor_id}_{i:06d}")
#     os.makedirs(pair_dir, exist_ok=True)
    
#     # Зберігаємо патчі та Гомографію
#     np.save(os.path.join(pair_dir, 'img1.npy'), patch_summer) 
#     np.save(os.path.join(pair_dir, 'img2.npy'), patch_other)
#     np.save(os.path.join(pair_dir, 'homography.npy'), h_gt) 
    
#     # Зберігаємо метадані
#     metadata = {
#         'img1_path': pair_data['summer_img']['tci_path'],
#         'img2_path': pair_data['other_img']['tci_path'],
#         'date_img1': pair_data['summer_img']['date'].isoformat(),
#         'date_img2': pair_data['other_img']['date'].isoformat(),
#         'season_pair': pair_data['season_pair'],
#         'deforestation_id': defor_id,
#         'centroid': pair_data['centroid'].__geo_interface__,
#         'tile': pair_data['tile'],
#     }
#     with open(os.path.join(pair_dir, 'metadata.json'), 'w') as f:
#         json.dump(metadata, f, indent=2)
        
#     return split # Повертаємо, до якого набору належить пара ('train' або 'val')

In [ ]:
# # ======================================================
# # ГОЛОВНА ЛОГІКА (З ЛІМІТОМ ТА ІТЕРАЦІЯМИ)
# # ======================================================
# def run_limited_generation():
    
#     print(f"⚙️ Використовуємо {NUM_WORKERS} процесорів.")
#     print(f"🎯 Ліміт тренувальних пар: {TRAIN_PAIRS_LIMIT}")
    
#     # Лічильники
#     train_count = 0
#     val_count = 0
#     total_pairs_processed = 0
    
#     # Налаштування директорій
#     os.makedirs(os.path.join(OUTPUT_DIR, 'train'), exist_ok=True)
#     os.makedirs(os.path.join(OUTPUT_DIR, 'val'), exist_ok=True)

#     # Використовуємо пул для запуску
#     with Pool(NUM_WORKERS) as pool:
        
#         # Ітерація над лінивим генератором
#         pair_iter = pair_generator()
        
#         # Запускаємо перший "батч" завдань, щоб пул не простоював
#         BATCH_SIZE = NUM_WORKERS * 4
        
#         # --- ФАЗА 1: Збір та запуск першого батчу (виправлено розпакування) ---
#         initial_tasks = []
        
#         # Правильне розпакування: (i, pair) повертає сам генератор
#         # Використовуємо next(pair_iter) для отримання наступного елемента
        
#         for _ in range(BATCH_SIZE):
#             try:
#                 # Генератор повертає: i, pair_data
#                 i, pair_data = next(pair_iter) 
                
#                 # Тепер pair_data є словником, а не кортежем, тому ['deforestation'] працює
#                 split = get_split(pair_data['deforestation']['id'])
                
#                 initial_tasks.append((i, pair_data, OUTPUT_DIR, PATCH_SIZE_FINAL, H_GT, split))
#                 total_pairs_processed += 1
#             except StopIteration:
#                 break # Генератор вичерпано раніше
#             except Exception:
#                 # Обробка помилок парсингу/отримання ID
#                 continue
            
#         print(f"⚡️ Запуск {len(initial_tasks)} початкових завдань...")
        
#         if not initial_tasks:
#             print("❌ Не вдалося згенерувати жодного початкового завдання. Перевірте файл JSONL.")
#             return

#         # Запускаємо перші завдання
#         async_results = pool.map_async(process_single_pair_limited, initial_tasks)
        
#         # --- ФАЗА 2: Основний цикл обробки ---
#         pbar = tqdm(total=TRAIN_PAIRS_LIMIT, desc="Створено TRAIN пар")
        
#         while train_count < TRAIN_PAIRS_LIMIT:
            
#             # 2. Очікуємо на результати попереднього батчу
#             try:
#                 # Очікуємо, поки буде готовий хоча б один результат
#                 if async_results.ready():
#                     results = async_results.get()
                    
#                     # 3. Оновлення лічильників та прогресу
#                     for split_result in results:
#                         if split_result == 'train':
#                             train_count += 1
#                         elif split_result == 'val':
#                             val_count += 1
                            
#                     pbar.update(train_count - pbar.n)
                    
#                     # 4. Перевірка ліміту
#                     if train_count >= TRAIN_PAIRS_LIMIT:
#                         break
                        
#                     # 5. Створення та запуск нового батчу завдань (виправлено розпакування)
#                     new_tasks = []
                    
#                     for _ in range(BATCH_SIZE):
#                         try:
#                             # Отримуємо наступний елемент
#                             i, pair_data = next(pair_iter) 
#                         except StopIteration:
#                             break # Генератор вичерпано
#                         except Exception:
#                             continue # Помилка при отриманні/парсингу наступного елемента

#                         split = get_split(pair_data['deforestation']['id'])
                        
#                         # Якщо це тренувальна пара і ми близькі до ліміту, не додаємо її
#                         if split == 'train' and train_count + len(new_tasks) >= TRAIN_PAIRS_LIMIT:
#                              break
                             
#                         new_tasks.append((i, pair_data, OUTPUT_DIR, PATCH_SIZE_FINAL, H_GT, split))
#                         total_pairs_processed += 1
                        
#                     if not new_tasks:
#                         break # Генератор вичерпано
                        
#                     async_results = pool.map_async(process_single_pair_limited, new_tasks)
                    
#             except Exception as e:
#                 # Обробка помилок пулу
#                 print(f"\nКритична помилка в пулі: {e}")
#                 break
            
#             # Якщо завдання не готове, чекаємо
#             if not async_results.ready():
#                 pbar.set_description(f"Обробка ({train_count} train / {val_count} val)")
#                 plt.pause(0.1) # Коротка пауза для оновлення GUI/потоків

#         pbar.close()

#     print(f"\n✅ ГЕНЕРАЦІЮ ЗАВЕРШЕНО.")
#     print(f"📊 Фінальний результат:")
#     print(f"   • Створено TRAIN пар: {train_count}")
#     print(f"   • Створено VAL пар: {val_count}")
#     print(f"   • Оброблені рядки з JSONL: {total_pairs_processed}")

In [ ]:
# run_limited_generation()

⚙️ Використовуємо 2 процесорів.
🎯 Ліміт тренувальних пар: 300000
⚡️ Запуск 8 початкових завдань...


KeyboardInterrupt: 